# Lung Lobes Segmentation

## Imports

In [ ]:
%matplotlib inline

import SimpleITK as sitk
import numpy as np
import matplotlib.pyplot as plt
import scipy as sp 
import gui
import cv2
import matplotlib.image as mpimg

# from mayavi import mlab
from scipy import signal
from myshow import myshow, myshow3d
from read_data import LoadData
from lung_segment import LungSegment
from vessel_segment import VesselSegment
from mpl_toolkits.mplot3d import Axes3D

## Read data

In [ ]:
# loading data
data_path = "resource/"
img_name = "lola11-01.mhd"
data = LoadData(data_path, img_name)
data.loaddata()

In [ ]:
print "the shape of image is ", data.image.GetSize()

## Lung Segmentation
Rescale the intensities and map them to [0,255]

In [ ]:
% matplotlib notebook

WINDOW_LEVEL = (1050,500)
ls = LungSegment(data.image)

# Convert image to uint8 for showing 
ls.conv_2_uint8(WINDOW_LEVEL)

# Set the seed point manually...
seed_pts = [(125,237,200), (369,237,200)]

# Compute region growing
ls.regiongrowing(seed_pts)

# showimg image
ls.image_showing("Region Growing Result")

Write the region growing image

In [ ]:
sitk.WriteImage(ls.temp_img, "seg_implicit_thresholds.mhd")

In [ ]:
# Morphological Operatinon (Closing)
ls.image_closing(7)

# write image
sitk.WriteImage(ls.temp_img, "img_closing.mhd")

In [ ]:
img_closing = sitk.ReadImage("img_closing.mhd") # reading the existed closing image 

# get the numpy array of the 3D closing image for future using
img_closing_ndarray = sitk.GetArrayFromImage(img_closing)

## Vasculature Segmentation

In [ ]:
# get the result of previous lung segmentation.
img_closing_ndarray = sitk.GetImageFromArray(img_closing_ndarray)

In [ ]:
vs = VesselSegment(original=data.image, closing=img_closing_ndarray)

In [ ]:
print "   Pricessing Generate lung mask..."
vs.generate_lung_mask(lunglabel=[1,-5000], offset = 0)

# Write image...
Lung_mask = sitk.GetImageFromArray(vs.img)
sitk.WriteImage(Lung_mask, "Lung_mask.mhd")

print "   Processing Downsampling..."
vs.downsampling()

print "   Processing Thresholding..."
vs.thresholding(thval=180)
down = sitk.GetImageFromArray(vs.temp_img)
sitk.WriteImage(down, "downsample.mhd")

print "   Processing Region Growing..."
vs.max_filter(filter_size=5)

In [ ]:
# save the vasculature-segmented image
filtered = sitk.GetImageFromArray(vs.temp_img)
sitk.WriteImage(filtered, "filtered.mhd")

In [ ]:
# convert to binary image
filtered = sitk.ReadImage("filtered.mhd")
filtered = sitk.GetArrayFromImage(filtered)
filtered[filtered > 0] = 1
binary_filtered = sitk.GetImageFromArray(filtered)
sitk.WriteImage(binary_filtered, "binary_filtered.mhd")

## Postprocessing for fissure enhancement
**Note:** the following steps need the result of fissure segmentation obtained by the C++ codes I provide. Since the SimpleITK package didn't provide enough functions for fissure segmentation (like computing 3D Hessian matrix), I used ITK C++ for this part, instead.

In [ ]:
import SimpleITK as sitk
from read_data import LoadData
import numpy as np
import collections

# Load the fissure image
data = LoadData(path="fissure_enhancement_cxx/", name="vessel_rg.mhd")
data.loaddata()
image = sitk.GetArrayFromImage(data.image)

In [ ]:
# count the volume for each label and remove the ones less than 5000.
nonzeros = image[image > 0]
d = collections.Counter( nonzeros )
val_key = []
keys = set([])
for key, val in d.items():
    if val > 5000:
        keys.add(key)

image[image == 0] = 1
for key in keys:
    image[image == key] = 0

image[image > 0] = 2
image[image == 0] = 1 # the regions left are set to 1
image[image == 2] = 0 # rest is 0
img = sitk.GetImageFromArray(image.astype(np.uint8))

In [ ]:
# Using closing to fill holes
size = 7
closing = sitk.BinaryMorphologicalClosingImageFilter()
closing.SetForegroundValue(255)
closing.SetKernelRadius(size)
img = closing.Execute(img)
# save results
sitk.WriteImage(img, "fissure_enhancement_cxx/voxel_val_region_growing_closing.mhd")

## Generate Label map for lung, vasculature and fissure regions

In [ ]:
lung_mask = LoadData(path="", name="Lung_mask.mhd")
lung_mask.loaddata()
fissure = LoadData(path="fissure_enhancement_cxx/", name="voxel_val_region_growing_closing.mhd")
fissure.loaddata()
vessel = LoadData(path="", name="binary_filtered.mhd")
vessel.loaddata()

In [ ]:
lung_mask = sitk.GetArrayFromImage(lung_mask.image)
fissure = sitk.GetArrayFromImage(fissure.image)
vessel = sitk.GetArrayFromImage(vessel.image)

In [ ]:
lung_mask[lung_mask != 0] = 3
lung_mask[vessel > 0] = 1
lung_mask[fissure > 0] = 2

In [ ]:
lung_mask = sitk.GetImageFromArray(lung_mask)
sitk.WriteImage(lung_mask, "label_map.mhd")